<a href="https://colab.research.google.com/github/napchick/mos_real_estate_bot/blob/main/model_training.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn import metrics
import time
import pickle
from scipy import stats

In [ ]:
!pip install optuna
import optuna

# Датасет: https://www.kaggle.com/datasets/egorkainov/moscow-housing-price-dataset

In [3]:
data2 = pd.read_csv('data 2.csv')

In [4]:
data2

Price Apartment type  Metro station  Minutes to metro  \
0       6300000.0      Secondary        Опалиха               6.0   
1       9000000.0      Secondary        Павшино               2.0   
2      11090000.0      Secondary       Мякинино              14.0   
3       8300000.0      Secondary       Строгино               8.0   
4       6450000.0      Secondary        Опалиха               6.0   
...           ...            ...            ...               ...   
22671   4768792.0   New building     Котельники               8.0   
22672   5900000.0   New building  Домодедовская              25.0   
22673   3700000.0   New building     Котельники              30.0   
22674   5768869.0   New building       Жулебино              14.0   
22675   6839157.0   New building     Котельники               8.0   

              Region  Number of rooms   Area  Living area  Kitchen area  \
0      Moscow region              1.0  30.60         11.1           8.5   
1      Moscow region              1.0  49.20         20.0          10.0   
2      Moscow region              1.0  44.70         16.2          13.1   
3      Moscow region              1.0  35.10         16.0          11.0   
4      Moscow region              1.0  37.70         15.2           4.0   
...              ...              ...    ...          ...           ...   
22671  Moscow region              0.0  31.75         13.0           5.0   
22672  Moscow region              1.0  31.60         10.1          12.2   
22673  Moscow region              0.0  18.00         15.0           8.1   
22674  Moscow region              2.0  36.39         22.0           6.6   
22675  Moscow region              2.0  56.13         32.0           5.0   

       Floor  Number of floors                 Renovation  
0       25.0                25                   Cosmetic  
1        6.0                15  European-style renovation  
2       10.0                25                   Cosmetic  
3       12.0                33  European-style renovation  
4        5.0                 5         Without renovation  
...      ...               ...                        ...  
22671    4.0                17                   Cosmetic  
22672   11.0                15                   Cosmetic  
22673   17.0                17                   Cosmetic  
22674   12.0                14                   Cosmetic  
22675   10.0                17                   Cosmetic  

[22676 rows x 12 columns]

# Работа с данными

In [ ]:
# проверка на наличие пропусков
data2.isna().sum()

Price               0
Apartment type      0
Metro station       0
Minutes to metro    0
Region              0
Number of rooms     0
Area                0
Living area         0
Kitchen area        0
Floor               0
Number of floors    0
Renovation          0
dtype: int64

In [5]:
# переименуем столбцы для более удобной работы
data2 = data2.rename(columns = {'Apartment type' : 'is_new', 'Metro station' : 'metro', 'Minutes to metro' : 'minutes', 'Number of rooms' : 'rooms', 'Living area' : 'liv_area',
                              'Kitchen area' : 'kit_area', 'Number of floors' : 'num_of_floors', 'Price' : 'price', 'Region':'is_moscow', 'Floor':'floor', 'Renovation':'renovation', 'Area' : 'area'})

# выбросим дубликаты
data2 = data2.drop_duplicates()
# закодируем столбцы, которые имеют только 2 значения
data2['is_new'] = data2['is_new'].apply(lambda x: 1 if x == 'New building' else 0)
data2['is_moscow'] = data2['is_moscow'].apply(lambda x: 1 if x == 'Moscow' else 0)

In [ ]:
# уберем выбросы
data2 = data2[(np.abs(stats.zscore(data2['price'])) < 3)]

In [ ]:
data2['metro'] = data2['metro'].str.lower().str.strip()

In [ ]:
# создадим списки административных округов москвы и заполним их станциями метро
vao = ["aвиамоторная", "андроновка", "белокаменная", "бульвар рокоссовского", "выхино", "измайлово", "измайловская", "кусоково", "локомотив", "лухмановская", "митьково", "новогиреево", "новокосино", "партизанская", "первомайская", "перово", "преображенская площадь", "семеновская", "соколиная гора", "сокольники", "улица дмитриевского", "черкизовская", "шоссе энтузиастов", "щелковская", "электрозаводская", "щёлковская"]
zao = ["филёвский парк", "немчиновка", "тропарёво", "аминьевская", "аэропорт внуково", "багратионовская", "боровское шоссе", "давыдково", "киевская", "кропоткинская", "крылатское", "кунцевская", "кутузовская", "ломоносовский проспект", "матвеевская", "мещерская", "минская", "мичуринский проспект", "молодежная", "молодёжная", "новаторская", "новопеределкино", "озёрная", "очаково", "парк победы", "переделкино", "пионерская", "поклонная", "проспект вернадского", "рабочий посёлок", "раменки", "сетунь", "славянский бульвар", "солнечная", "солнцево", "студенческая", "тропарево", "филевский парк", "фили", "юго-западная"]
nmao = ["коммунарка", "внуково", "говорово", "кокошкино", "крёкшино", "мичиуринец", "новомосковская", "ольховая", "остафьево", "потапово", "прокшино", "пыхтино", "рассказовка", "румянцево", "саларьево", "санино", "толстопальцево", "тютчевская", "филатов луг", "щербинка"]
sao = ["новодачная","аэропорт", "балтийская", "беговая", "беломорская", "бескудниково", "верхние лихоборы", "водный стадион", "войковская", "гражданская", "грачёвская", "дегунино", "динамо", "дмитровская", "зорге", "коптево", "красный балтиец", "лихоборы", "марк", "молжаниново", "москова-сити", "моссельмаш", "новоподрезково", "окружная", "панфиловская", "петровский парк", "петровско-разумовская", "полежаевская", "речной вокзал", "савеловская", "селигерская", "сокол", "стрешнево", "тимирязевская", "ховрино", "хорошёво", "хорошево", "хорошёвская", "цска", "яхромская"]
svao = ["марьина роща (шереметьевская)","алексеевская", "алтуфьево", "бабушкинская", "бибирево", "ботанический сад", "бутырская", "вднх", "владыкино", "выставочный центр", "лианозово", "марьина роща", "медведково", "окружная", "останкино", "отрадное", "ростокино", "савеловская", "савёловская", "свиблово", "телецентр", "улица академика королёва", "улица милашенкова", "улица сергея эйзенштейна", "физтех", "фонвизинская"]
szao = ["нахабино", "аникеевка", "мякинино", "красногорская","павшино", "опалиха", "волоколамская", "митино", "мнёвники", "народное ополчение", "октябрьское поле", "пенягино", "планерная", "пятницкое шоссе", "спартак", "строгино", "сходненская", "терехово", "трикотажная", "тушинская", "щукинская", "карамышевская"]
cao = ["международная", "деловой центр","александровский сад", "арбатская", "баррикадная", "бауманская", "беговая", "белорусская", "библиотека имени ленина", "боровицкая", "воробьевы горы", "выставочная", "добрынинская", "достоевская", "китай-город", "комсомольская", "краснопресненская", "красносельская", "красные ворота", "крестьянская застава", "кузнецкий мост", "курская", "лубянка", "лужники", "марксистская", "маяковская", "менделеевская", "москва-сити", "новокузнецкая", "новослободская", "октябрьская", "охотный ряд", "павелецкая", "парк культуры", "площадь ильича", "площадь революции", "площадь трёх вокзалов", "полянка", "пролетарская", "проспект мира", "пушкинская", "рижская", "римская", "серп и молот", "серпуховская", "смоленская", "спортивная", "сретенский бульвар", "сухаревская", "таганская", "тверская", "театральная", "тестовская", "третьяковская", "трубная", "тургеневская", "улица 1905 года", "фрунзенская", "цветной бульвар", "чеховская", "чистые пруды", "чкаловская", "шелепиха", "электрозаводская", "воробьёвы горы", "библиотека им. ленина", "библиотека и ленина"]
uvao = ["авиамоторная", "андроновка", "братиславская", "битца", "волгоградский проспект", "волжская", "выхино", "депо", "дубровка", "жулебино", "калитники", "кожуховская", "косино", "котельники", "кузьминки", "курьяново", "лермонтовский проспект", "лефортово", "люблино", "марьино", "москва-товарная", "некрасовка", "нижегородская", "новохохловская", "окская", "перерва", "печатники", "плющево", "рязанский проспект", "сортировочная", "стахановская", "текстильщики", "угрешская", "чухлинка", "юго-восточная"]
uzao = ["тёплый стан", "силикатная","академическая", "беляево", "битцевский парк", "бульвар адмирала ушакова", "бульвар дмитрия донского", "бунинская аллея", "бутово", "воронцовская", "генерала тюленева", "зюзино", "калужская", "каховская", "коньково", "нахимовский проспект", "новаторская", "новоясеневская", "новые черемушки", "площадь гагарина", "профсоюзная", "севастопольская", "теплый стан", "улица горчакова", "улица скобелевская", "улица старокачаловская", "университет", "университет дружбы народов", "ясенево", "новые черёмушки"]
uao = ["варшавская (коломенское)", "автозаводская", "автозаводская", "алма-атинская", "аннино", "борисово", "варшавская", "верхние котлы", "домодедовская", "зил", "зябликово", "кантемировская", "каширская", "каширская", "кленовый бульвар", "коломенская", "красногвардейская", "красный строитель", "крымская", "ленинский проспект", "лесопарковая", "москворечье", "нагатинская", "нагатинский затон", "нагорная", "орехово", "покровское", "пражская", "технопарк", "тульская", "улица академика янгеля", "царицыно", "царицыно", "чертановская", "шаболовская", "шипиловская", "южная"]





In [ ]:
# сделаем словарь с административными районами
rayons = {'vao' : vao, 'zao' : zao, 'nmao' : nmao, 'sao' : sao, 'svao' : svao,
          'szao' : szao, 'cao' : cao, 'uvao' : uvao, 'uzao' : uzao, 'uao' : uao}

In [ ]:
# создадим новый столбец для определения административного района квартиры
data2['district'] = '-'

In [ ]:
# функция, которая по метро определяет ее АО
def find(value):
  for ray in rayons:
    if value in rayons[ray]:
      return ray

data2['district'] = data2['metro'].apply(find)

In [ ]:
# удалим столбец с живой площадью, тк он линейно зависим с общей площадью
data2.drop(columns=['liv_area'], inplace=True)

In [ ]:
data2

price  is_new          metro  minutes  is_moscow  rooms   area  \
0       6300000.0       0        опалиха      6.0          0    1.0  30.60   
1       9000000.0       0        павшино      2.0          0    1.0  49.20   
2      11090000.0       0       мякинино     14.0          0    1.0  44.70   
3       8300000.0       0       строгино      8.0          0    1.0  35.10   
4       6450000.0       0        опалиха      6.0          0    1.0  37.70   
...           ...     ...            ...      ...        ...    ...    ...   
22670   5884024.0       1     котельники      8.0          0    1.0  44.17   
22672   5900000.0       1  домодедовская     25.0          0    1.0  31.60   
22673   3700000.0       1     котельники     30.0          0    0.0  18.00   
22674   5768869.0       1       жулебино     14.0          0    2.0  36.39   
22675   6839157.0       1     котельники      8.0          0    2.0  56.13   

       kit_area  floor  num_of_floors                 renovation district  
0           8.5   25.0             25                   Cosmetic     szao  
1          10.0    6.0             15  European-style renovation     szao  
2          13.1   10.0             25                   Cosmetic     szao  
3          11.0   12.0             33  European-style renovation     szao  
4           4.0    5.0              5         Without renovation     szao  
...         ...    ...            ...                        ...      ...  
22670      10.3    4.0             17                   Cosmetic     uvao  
22672      12.2   11.0             15                   Cosmetic      uao  
22673       8.1   17.0             17                   Cosmetic     uvao  
22674       6.6   12.0             14                   Cosmetic     uvao  
22675       5.0   10.0             17                   Cosmetic     uvao  

[20432 rows x 12 columns]

In [ ]:
#в москве
data2[data2['is_moscow'] == 1].groupby(['district'])['price'].describe()

count          mean           std        min         25%  \
district                                                              
cao       2118.0  8.476107e+07  6.792859e+07  2390000.0  29000000.0   
nmao       664.0  1.345037e+07  7.332338e+06  2650000.0   8487500.0   
sao       1530.0  2.965108e+07  3.241152e+07  2600000.0  11500000.0   
svao       764.0  1.788529e+07  1.617676e+07  2700000.0   8512067.5   
szao       627.0  3.395852e+07  4.131289e+07  3600000.0  13495000.0   
uao       1908.0  2.225661e+07  1.977513e+07  1150000.0  12202617.5   
uvao      3426.0  1.072698e+07  5.156017e+06  1420000.0   7968030.0   
uzao       759.0  2.369480e+07  2.782409e+07  1750000.0  10000000.0   
vao        758.0  1.573652e+07  1.365772e+07  2799000.0   8699250.0   
zao       1798.0  5.532953e+07  5.782700e+07  2900000.0  16402500.0   

                 50%          75%          max  
district                                        
cao       64427206.5  126429202.0  272402200.0  
nmao      11495000.0   15912500.0   85000000.0  
sao       18990000.0   33597725.0  250000000.0  
svao      13800000.0   21000000.0  165000000.0  
szao      19900000.0   35999500.0  258000000.0  
uao       16479744.0   24000000.0  230000000.0  
uvao      10016580.0   12001582.5   56000000.0  
uzao      15200000.0   24920000.0  223807250.0  
vao       12500000.0   17500000.0  103891410.0  
zao       32250000.0   69900000.0  270000000.0

Подели Москву на 3 района:

- zao, cao, szao
- sao, uao, uzao
- nmao, uvao, vao, svao


In [ ]:
#в области
data2[data2['is_moscow'] == 0].groupby(['district'])['price'].describe()

count          mean           std        min        25%  \
district                                                             
szao       634.0  1.078964e+07  4.432776e+06  4200000.0  8006426.0   
uao       3339.0  6.542585e+06  2.200947e+06  1939125.0  5182880.5   
uvao      1986.0  6.724485e+06  2.174600e+06  2261523.0  5261100.0   
uzao       109.0  6.596419e+06  2.059595e+06  3386249.0  5428951.0   

                 50%          75%         max  
district                                       
szao      10195000.0  12385955.25  53000000.0  
uao        6326844.0   7662490.00  18877250.0  
uvao       6251150.0   7821967.50  24340000.0  
uzao       6071913.0   7413824.00  16500000.0

In [ ]:
# Делим наши данные на районы
moscow_high = data2[(data2['is_moscow'] == 1) & ((data2['district'] == 'zao') | (data2['district'] == 'cao'))]
moscow_medium = data2[(data2['is_moscow'] == 1) & ((data2['district'] == 'sao') | (data2['district'] == 'szao') | (data2['district'] == 'uzao') | (data2['district'] == 'uao'))]
moscow_low = data2[(data2['is_moscow'] == 1) & ((data2['district'] == 'nmao') | (data2['district'] == 'uvao') | (data2['district'] == 'vao') | (data2['district'] == 'svao'))]
region = data2[data2['is_moscow'] == 0]


In [ ]:
# удаляем столбцы индекс москвы и. метро, тк они больше не нужны
moscow_high.drop(columns=['is_moscow', 'metro'], inplace=True)
moscow_medium.drop(columns=['is_moscow', 'metro'], inplace=True)
moscow_low.drop(columns=['is_moscow', 'metro'], inplace=True)
region.drop(columns=['is_moscow', 'metro', 'district'], inplace=True)

<ipython-input-49-ba45afd5dbe8>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  moscow_high.drop(columns=['is_moscow', 'metro'], inplace=True)
<ipython-input-49-ba45afd5dbe8>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  moscow_medium.drop(columns=['is_moscow', 'metro'], inplace=True)
<ipython-input-49-ba45afd5dbe8>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  moscow_low.drop(columns=['is_moscow', 'metro'], inplace=True)
<ipyth

In [ ]:
prices = pd.concat([moscow_high['price'].describe(), moscow_medium['price'].describe(), moscow_low['price'].describe(), region['price'].describe() ], axis=1)

In [ ]:
# сравним цены в разных районах
prices.columns = ['high', 'medium', 'low', 'region']
prices

high        medium           low        region
count  3.916000e+03  4.824000e+03  5.612000e+03  6.068000e+03
mean   7.124781e+07  2.634911e+07  1.270034e+07  7.046829e+06
std    6.515513e+07  2.914752e+07  9.522664e+06  2.824807e+06
min    2.390000e+06  1.150000e+06  1.420000e+06  1.939125e+06
25%    2.117500e+07  1.190000e+07  8.059320e+06  5.325677e+06
50%    4.790000e+07  1.700000e+07  1.076588e+07  6.580620e+06
75%    1.000000e+08  2.802750e+07  1.400000e+07  8.112109e+06
max    2.724022e+08  2.580000e+08  1.650000e+08  5.300000e+07

In [ ]:
moscow_high.to_csv('moscow_high.csv')
moscow_medium.to_csv('moscow_medium.csv')
moscow_low.to_csv('moscow_low.csv')
region.to_csv('region.csv')

# Catboost для moscow_high

In [ ]:
!pip uninstall catboost
!pip install catboost

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.7/98.7 MB 7.9 MB/s eta 0:00:00


In [ ]:
import catboost
from catboost import *

In [ ]:
X_ch = moscow_high.drop(columns=['price'])
y_ch = moscow_high.price

X_train_high_c, X_test_high_c, y_train_high_c, y_test_high_c = train_test_split(X_ch, y_ch, train_size = 0.7, shuffle=True, random_state=13)
cat_features = [7, 8]

In [ ]:
from catboost import CatBoostRegressor

model = CatBoostRegressor(
    iterations=1000,
    learning_rate=0.1,
    loss_function='Quantile:alpha=0.25',
    use_best_model=True,
    random_seed=13
)
model.fit(
    X_train_high_c, y_train_high_c,
    cat_features=cat_features,
    eval_set=(X_test_high_c, y_test_high_c),
    verbose=False
)
print('Model is fitted: ' + str(model.is_fitted()))
print('Model params:')
print(model.get_params())

Model is fitted: True
Model params:
{'iterations': 1000, 'learning_rate': 0.1, 'loss_function': 'Quantile:alpha=0.25', 'random_seed': 13, 'use_best_model': True}


In [ ]:
# функция, которая обучает модель и выводит ошибку
def mlf_c(alg, X_train, X_test, y_train, y_test, cat_features, early_stopping_rounds=50):

  #Fit the algorithm on the data
  alg.fit(
    X_train, y_train,
    cat_features=cat_features,
    eval_set=(X_test, y_test),
    verbose=False
  )

  #Predict training set:
  dtrain_predictions = alg.predict(X_train)

  #Print model report:
  print("\nModel Report")
  print(f"RMSE for train: {metrics.root_mean_squared_error(y_train, dtrain_predictions)}")
  print(f"r2 for train: {metrics.r2_score(y_train, dtrain_predictions)}, \n")

  #Predict on testing data:
  dtest_predictions = alg.predict(X_test)
  print(f"RMSE for test: {metrics.root_mean_squared_error(y_test, dtest_predictions)}")
  print(f"r2 for test: {metrics.r2_score(y_test, dtest_predictions)}")

In [ ]:
mlf_c(model, X_train_high_c, X_test_high_c, y_train_high_c, y_test_high_c, cat_features)


Model Report
RMSE for train: 34464417.160647705
r2 for train: 0.7215839238111983, 

RMSE for test: 38121996.72611432
r2 for test: 0.653248603561732


In [ ]:
# функция библиотеки optuna, которая позволяет перебирать различные показатели параметров и находить лучшее сочетание
def objective(trial):
    params = {
        "iterations": trial.suggest_int("iterations", 500, 1200),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 0.1, log=True),
        "depth": trial.suggest_int("depth", 7, 13),
        "subsample": trial.suggest_float("subsample", 0.5, 1.0),
        "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.5, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 45),
    }

    model = CatBoostRegressor(**params, loss_function='Quantile:alpha=0.7', silent=True, random_seed=13)
    model.fit(X_train_high_c, y_train_high_c, cat_features=cat_features, eval_set=(X_test_high_c, y_test_high_c))
    predictions = model.predict(X_test_high_c)
    rmse = metrics.mean_squared_error(y_test_high_c, predictions, squared=False)
    return rmse

In [ ]:
study = optuna.create_study(direction='minimize')
study.optimize(objective, n_trials=30)

[I 2024-12-10 15:26:14,789] A new study created in memory with name: no-name-80029f44-bd38-4f62-9ad8-00116ff2b84c
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-10 15:26:20,054] Trial 0 finished with value: 33488972.249540295 and parameters: {'iterations': 723, 'learning_rate': 0.014031421737107834, 'depth': 8, 'subsample': 0.7337361427745361, 'colsample_bylevel': 0.9637541778906107, 'min_data_in_leaf': 26}. Best is trial 0 with value: 33488972.249540295.
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-10 15:26:54,860] Trial 1 finished with value:

In [ ]:
print('Best hyperparameters:', study.best_params)
print('Best RMSE:', study.best_value)

Best hyperparameters: {'iterations': 634, 'learning_rate': 0.060779009831171696, 'depth': 13, 'subsample': 0.782229238657602, 'colsample_bylevel': 0.6153297786329257, 'min_data_in_leaf': 10}
Best RMSE: 30056297.482409194


In [ ]:
################# itog ########################
model2 = CatBoostRegressor(iterations=1187, learning_rate=0.02819599939563895, depth=13, colsample_bylevel=0.9493374291903622,
                          subsample = 0.7306108384522604, min_data_in_leaf=17, loss_function='Quantile:alpha=0.7',
                           use_best_model=True, random_seed=13)
mlf_c(model2, X_train_high_c, X_test_high_c, y_train_high_c, y_test_high_c, cat_features)


Model Report
RMSE for train: 12971487.376599036
r2 for train: 0.960560446787156, 

RMSE for test: 30027005.21001366
r2 for test: 0.7848749531348375


In [ ]:
# сохраняем модель в файл
filename = 'catboost_high'
pickle.dump(model2, open(filename, 'wb'))

In [ ]:
# проверка работы файла с моделью
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_high_c)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_high_c, y_pred)))

root mean squared error :  30027005.21001366


#Catboost для moscow_medium

In [ ]:
X_cm = moscow_medium.drop(columns=['price'])
y_cm = moscow_medium.price

X_train_medium_c, X_test_medium_c, y_train_medium_c, y_test_medium_c = train_test_split(X_cm, y_cm, train_size = 0.7, shuffle=True, random_state=13)
cat_features = [7, 8]

In [ ]:
model_cm = CatBoostRegressor(
    iterations=1000,
    learning_rate=0.1,
    loss_function='Quantile:alpha=0.75',
    use_best_model=True,
    random_seed=13
)
model_cm.fit(
    X_train_medium_c, y_train_medium_c,
    cat_features=cat_features,
    eval_set=(X_test_medium_c, y_test_medium_c),
    verbose=False
)
print('Model is fitted: ' + str(model_cm.is_fitted()))
print('Model params:')
print(model_cm.get_params())

Model is fitted: True
Model params:
{'iterations': 1000, 'learning_rate': 0.1, 'loss_function': 'Quantile:alpha=0.75', 'random_seed': 13, 'use_best_model': True}


In [ ]:
mlf_c(model_cm, X_train_medium_c, X_test_medium_c, y_train_medium_c, y_test_medium_c, cat_features)


Model Report
RMSE for train: 10521008.840880152
r2 for train: 0.930705072679851, 

RMSE for test: 14514808.326629099
r2 for test: 0.8535167624101687


In [ ]:
def objective_cm(trial):
    params = {
        "iterations": trial.suggest_int("iterations", 300, 1200),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 0.1, log=True),
        "depth": trial.suggest_int("depth", 3, 15),
        "subsample": trial.suggest_float("subsample", 0.5, 1.0),
        "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.5, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 55),
    }

    model = CatBoostRegressor(**params, loss_function='Quantile:alpha=0.7', silent=True,  random_seed=13)
    model.fit(X_train_medium_c, y_train_medium_c, cat_features=cat_features, eval_set=(X_test_medium_c, y_test_medium_c))
    predictions = model.predict(X_test_medium_c)
    rmse = metrics.mean_squared_error(y_test_medium_c, predictions, squared=False)
    return rmse

In [ ]:
study_cm = optuna.create_study(direction='minimize')
study_cm.optimize(objective_cm, n_trials=30)

[I 2024-12-10 19:24:00,064] A new study created in memory with name: no-name-3152bf0f-f508-4c86-a4c0-575db698b38e
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-10 19:25:44,017] Trial 0 finished with value: 12269975.81640367 and parameters: {'iterations': 428, 'learning_rate': 0.09439360147381169, 'depth': 14, 'subsample': 0.6620871162499453, 'colsample_bylevel': 0.7571423432296305, 'min_data_in_leaf': 13}. Best is trial 0 with value: 12269975.81640367.
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-10 19:25:45,068] Trial 1 finished with value: 2

In [ ]:
print('Best hyperparameters:', study_cm.best_params)
print('Best RMSE:', study_cm.best_value)

Best hyperparameters: {'iterations': 933, 'learning_rate': 0.020555797321524513, 'depth': 11, 'subsample': 0.993428256907132, 'colsample_bylevel': 0.6615245306141675, 'min_data_in_leaf': 19}
Best RMSE: 10804278.551622849


In [ ]:
################# itog ########################
model_cm1 = CatBoostRegressor(iterations=933, learning_rate=0.020555797321524513, depth=11, colsample_bylevel=0.6615245306141675,
                          subsample = 0.993428256907132, min_data_in_leaf=19, loss_function='Quantile:alpha=0.7',
                             use_best_model=True, random_seed=13)
mlf_c(model_cm1, X_train_medium_c, X_test_medium_c, y_train_medium_c, y_test_medium_c, cat_features)


Model Report
RMSE for train: 6694789.273850664
r2 for train: 0.950812142841678, 

RMSE for test: 10804278.551622849
r2 for test: 0.8342309826192591


In [ ]:
filename = 'catboost_medium'
pickle.dump(model_cm1, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_medium_c)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_medium_c, y_pred)))

root mean squared error :  10804278.551622849


# Catboost для moscow_low

In [ ]:
X_cl = moscow_low.drop(columns=['price'])
y_cl = moscow_low.price

X_train_low_c, X_test_low_c, y_train_low_c, y_test_low_c = train_test_split(X_cl, y_cl, train_size = 0.7, shuffle=True, random_state=13)
cat_features = [7, 8]

In [ ]:
model_cl = CatBoostRegressor(
    iterations=1000,
    learning_rate=0.1,
    use_best_model=True,
    random_seed=13
)
model_cl.fit(
    X_train_low_c, y_train_low_c,
    cat_features=cat_features,
    eval_set=(X_test_low_c, y_test_low_c),
    verbose=False
)
print('Model is fitted: ' + str(model_cl.is_fitted()))
print('Model params:')
print(model_cl.get_params())

Model is fitted: True
Model params:
{'iterations': 1000, 'learning_rate': 0.1, 'loss_function': 'RMSE', 'random_seed': 13, 'use_best_model': True}


In [ ]:
mlf_c(model_cl, X_train_low_c, X_test_low_c, y_train_low_c, y_test_low_c, cat_features)

NameError: name 'model_cl' is not defined

In [ ]:
def objective_cl(trial):
    params = {
        "iterations": trial.suggest_int("iterations", 300, 650),
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "depth": trial.suggest_int("depth", 5, 11),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.7, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 25),
    }

    model = CatBoostRegressor(**params, loss_function='Quantile:alpha=0.7', silent=True, random_seed=13)
    model.fit(X_train_low_c, y_train_low_c, cat_features=cat_features, eval_set=(X_test_low_c, y_test_low_c))
    predictions = model.predict(X_test_low_c)
    rmse = metrics.mean_squared_error(y_test_low_c, predictions, squared=False)
    return rmse

In [ ]:
study_cl = optuna.create_study(direction='minimize')
study_cl.optimize(objective_cl, n_trials=30)

[I 2024-12-10 20:33:45,595] A new study created in memory with name: no-name-5da96df7-ab9f-436f-ad9e-4c389fc43ca3
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-10 20:33:53,716] Trial 0 finished with value: 5270124.45834105 and parameters: {'iterations': 416, 'learning_rate': 0.003594737322683029, 'depth': 9, 'subsample': 0.8576353980884295, 'colsample_bylevel': 0.9457291707149595, 'min_data_in_leaf': 6}. Best is trial 0 with value: 5270124.45834105.
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-10 20:33:58,530] Trial 1 finished with value: 3431

In [ ]:
print('Best hyperparameters:', study_cl.best_params)
print('Best RMSE:', study_cl.best_value)

Best hyperparameters: {'iterations': 511, 'learning_rate': 0.0554777497089571, 'depth': 7, 'subsample': 0.7485132388324797, 'colsample_bylevel': 0.8968616894114306, 'min_data_in_leaf': 15}
Best RMSE: 2955016.5138541143


In [ ]:
################# itog ########################
model_cl1 = CatBoostRegressor(iterations=382, learning_rate=0.08473905607043009, depth=7, colsample_bylevel=0.9086604158965087,
                          subsample = 0.7101117118400826, min_data_in_leaf=7, loss_function='Quantile:alpha=0.7',
                             use_best_model=True, random_seed=13)
mlf_c(model_cl1, X_train_low_c, X_test_low_c, y_train_low_c, y_test_low_c, cat_features)


Model Report
RMSE for train: 2022651.3334671925
r2 for train: 0.953799243207533, 

RMSE for test: 2866820.124187761
r2 for test: 0.9139270653296961


In [ ]:
filename = 'catboost_low'
pickle.dump(model_cl1, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_low_c)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_low_c, y_pred)))

root mean squared error :  2866820.124187761


# Catboost для region

In [ ]:
X_c = region.drop(columns=['price'])
y_c = region.price

X_train_region_c, X_test_region_c, y_train_region_c, y_test_region_c = train_test_split(X_c, y_c, train_size = 0.7, shuffle=True, random_state=13)
cat_features = [7]

In [ ]:
model_r = CatBoostRegressor(
    iterations=1000,
    learning_rate=0.1,
    use_best_model=True,
    random_seed=13
)
model_r.fit(
    X_train_region_c, y_train_region_c,
    cat_features=cat_features,
    eval_set=(X_test_region_c, y_test_region_c),
    verbose=False
)
print('Model is fitted: ' + str(model_r.is_fitted()))
print('Model params:')
print(model_r.get_params())

Model is fitted: True
Model params:
{'iterations': 1000, 'learning_rate': 0.1, 'loss_function': 'RMSE', 'random_seed': 13, 'use_best_model': True}


In [ ]:
mlf_c(model_r, X_train_region_c, X_test_region_c, y_train_region_c, y_test_region_c, cat_features)


Model Report
RMSE for train: 460707.21664547356
r2 for train: 0.9725563829041587, 

RMSE for test: 778353.0279273406
r2 for test: 0.9290729293799344


In [ ]:
def objective_cr(trial):
    params = {
        "iterations": trial.suggest_int('iterations', 300, 800),
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "depth": trial.suggest_int("depth", 3, 12),
        "subsample": trial.suggest_float("subsample", 0.5, 0.9),
        "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.5, 0.9),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 15, 60),
    }

    model = CatBoostRegressor(**params,loss_function='Quantile:alpha=0.7', silent=True, random_seed=13)
    model.fit(X_train_region_c, y_train_region_c, cat_features=cat_features, eval_set=(X_test_region_c, y_test_region_c))
    predictions = model.predict(X_test_region_c)
    rmse = metrics.mean_squared_error(y_test_region_c, predictions, squared=False)
    return rmse

In [ ]:
study_cr = optuna.create_study(direction='minimize')
study_cr.optimize(objective_cr, n_trials=30)

[I 2024-12-11 10:16:13,949] A new study created in memory with name: no-name-bead46c7-51d2-4315-95b9-581e8b226e85
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:16:15,491] Trial 0 finished with value: 1210291.2157128486 and parameters: {'iterations': 748, 'learning_rate': 0.0418901865009603, 'depth': 3, 'subsample': 0.6059974960283089, 'colsample_bylevel': 0.6240731342041167, 'min_data_in_leaf': 25}. Best is trial 0 with value: 1210291.2157128486.
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:16:16,999] Trial 1 finished with value: 1

In [ ]:
print('Best hyperparameters:', study_cr.best_params)
print('Best RMSE:', study_cr.best_value)

Best hyperparameters: {'iterations': 642, 'learning_rate': 0.09929711100490832, 'depth': 11, 'subsample': 0.5901319897111447, 'colsample_bylevel': 0.7657985346856296, 'min_data_in_leaf': 15}
Best RMSE: 949262.0563354484


In [ ]:
################# itog ########################
model_r2 = CatBoostRegressor(iterations=489, learning_rate=0.07030189179042852, depth=10, colsample_bylevel=0.8247620784036073,
                          subsample = 0.754756387433371, min_data_in_leaf=24, loss_function='Quantile:alpha=0.7',
                            use_best_model=True, random_seed=13)
mlf_c(model_r2, X_train_region_c, X_test_region_c, y_train_region_c, y_test_region_c, cat_features)


Model Report
RMSE for train: 604162.6960539407
r2 for train: 0.952804658446056, 

RMSE for test: 925287.234766578
r2 for test: 0.8997667237109657


In [ ]:
filename = 'catboost_region'
pickle.dump(model_r2, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_region_c)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_region_c, y_pred)))

root mean squared error :  925287.234766578


# Lightgbm для moscow_high

In [ ]:
!pip install lightgbm
!arch -arm64 brew install libomp

arch: invalid option -- 'a'
Try 'arch --help' for more information.


In [ ]:
import lightgbm as lgb
from lightgbm import LGBMRegressor

/usr/local/lib/python3.10/dist-packages/dask/dataframe/__init__.py:42: FutureWarning: 
Dask dataframe query planning is disabled because dask-expr is not installed.

You can install it with `pip install dask[dataframe]` or `conda install dask`.
This will raise in a future version.

  warnings.warn(msg, FutureWarning)


In [ ]:
moscow_high_l = pd.get_dummies(moscow_high, columns=['renovation', 'district'], drop_first=True, dtype='int64')
X_lh = moscow_high_l.drop(columns=['price'])
y_lh = moscow_high_l.price

X_train_high_l, X_test_high_l, y_train_high_l, y_test_high_l = train_test_split(X_lh, y_lh, train_size = 0.7, shuffle=True, random_state=13)

In [ ]:
X_lh

is_new  minutes  rooms   area  kit_area  floor  num_of_floors  \
314         0      5.0    3.0  108.8      15.6    3.0              3   
315         0      9.0    3.0   96.9      11.1    2.0              5   
316         0      6.0    3.0   63.2      11.9   40.0             41   
317         0      6.0    3.0  145.0      18.6    3.0              6   
318         0      9.0    3.0  103.8      15.0    6.0              6   
...       ...      ...    ...    ...       ...    ...            ...   
13125       0      7.0    0.0   31.6       9.3    2.0              6   
13132       0      5.0    0.0   32.5       6.0    4.0             42   
13135       0     11.0    0.0   20.0       8.3   15.0             17   
13138       0      7.0    0.0   23.2       7.0    4.0             23   
13149       0     17.0    0.0   30.0       9.1   14.0             25   

       renovation_Designer  renovation_European-style renovation  \
314                      0                                     0   
315                      0                                     0   
316                      1                                     0   
317                      1                                     0   
318                      0                                     0   
...                    ...                                   ...   
13125                    0                                     0   
13132                    0                                     0   
13135                    0                                     0   
13138                    0                                     0   
13149                    0                                     0   

       renovation_Without renovation  district_zao  
314                                1             0  
315                                1             0  
316                                0             1  
317                                0             0  
318                                1             0  
...                              ...           ...  
13125                              0             0  
13132                              1             1  
13135                              0             0  
13138                              0             1  
13149                              0             1  

[3916 rows x 11 columns]

In [ ]:
gbm = LGBMRegressor(num_leaves=31,
                    learning_rate=0.05,
                    n_estimators=20,
                    random_state=13)
gbm.fit(X_train_high_l, y_train_high_l,
        eval_set=[(X_test_high_l, y_test_high_l)],
        eval_metric='rmse')

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000433 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 689
[LightGBM] [Info] Number of data points in the train set: 3007, number of used features: 12
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 106357113.690057


LGBMRegressor(learning_rate=0.05, n_estimators=20, random_state=13)

In [ ]:
def mlf_l(alg, X_train, X_test, y_train, y_test, early_stopping_rounds=50):

  #Fit the algorithm on the data
  alg.fit(
    X_train, y_train,
    eval_set=(X_test, y_test),
    eval_metric='rmse'
  )

  #Predict training set:
  dtrain_predictions = alg.predict(X_train)

  #Print model report:
  print("\nModel Report")
  print(f"RMSE for train: {metrics.root_mean_squared_error(y_train, dtrain_predictions)}")
  print(f"r2 for train: {metrics.r2_score(y_train, dtrain_predictions)}, \n")

  #Predict on testing data:
  dtest_predictions = alg.predict(X_test)
  print(f"RMSE for test: {metrics.root_mean_squared_error(y_test, dtest_predictions)}")
  print(f"r2 for test: {metrics.r2_score(y_test, dtest_predictions)}")

In [ ]:
mlf_l(gbm, X_train_high_l, X_test_high_l, y_train_high_l, y_test_high_l)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000087 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 689
[LightGBM] [Info] Number of data points in the train set: 3007, number of used features: 12
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 106357113.690057

Model Report
RMSE for train: 91378849.26046628
r2 for train: 0.6118481388509368, 

RMSE for test: 94698490.45665522
r2 for test: 0.6093891236685187


In [ ]:
def objective_lh(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 300, 700),
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 5, 13),
        "num_leaves": trial.suggest_int("num_leaves", 55, 90),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 3, 30),
    }

    model = LGBMRegressor(**params, objective='quantile', alpha=0.8, random_state=13)
    model.fit(X_train_high_l, y_train_high_l, eval_set=(X_test_high_l, y_test_high_l), eval_metric='rmse')
    predictions = model.predict(X_test_high_l)
    rmse = metrics.mean_squared_error(y_test_high_l, predictions, squared=False)
    return rmse

In [ ]:
study_lh = optuna.create_study(direction='minimize')
study_lh.optimize(objective_lh, n_trials=30)

[I 2024-12-11 10:32:08,591] A new study created in memory with name: no-name-fa0ea380-0222-4412-b171-8e201d8efc39


[LightGBM] [Warning] min_data_in_leaf is set=13, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=13, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=13
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000372 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 674
[LightGBM] [Info] Number of data points in the train set: 2741, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=13, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 122000016.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positiv

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:32:09,051] Trial 0 finished with value: 54326434.432775326 and parameters: {'n_estimators': 350, 'learning_rate': 0.0020172165820408366, 'max_depth': 5, 'num_leaves': 87, 'subsample': 0.9749142203064184, 'colsample_bytree': 0.6499199289758831, 'min_data_in_leaf': 13}. Best is trial 0 with value: 54326434.432775326.


[LightGBM] [Warning] min_data_in_leaf is set=13, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=13
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000403 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 674
[LightGBM] [Info] Number of data points in the train set: 2741, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=12, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=12
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 122000016.000000
[Lig

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:32:09,739] Trial 1 finished with value: 34158037.35822899 and parameters: {'n_estimators': 410, 'learning_rate': 0.06665484202898861, 'max_depth': 10, 'num_leaves': 58, 'subsample': 0.7762366913513351, 'colsample_bytree': 0.96207816475981, 'min_data_in_leaf': 12}. Best is trial 1 with value: 34158037.35822899.


...

[LightGBM] [Warning] min_data_in_leaf is set=9, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=9
[LightGBM] [Warning] min_data_in_leaf is set=13, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=13, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=13
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000449 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 674
[LightGBM] [Info] Number of data points in the train set: 2741, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=13, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 122000016.000000
[Light

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:32:42,677] Trial 28 finished with value: 32878380.5844362 and parameters: {'n_estimators': 667, 'learning_rate': 0.029845969417824515, 'max_depth': 13, 'num_leaves': 73, 'subsample': 0.9057214208437635, 'colsample_bytree': 0.9361641722757978, 'min_data_in_leaf': 13}. Best is trial 26 with value: 31589136.339236822.


[LightGBM] [Warning] min_data_in_leaf is set=11, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=11
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=11, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=11
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000083 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 674
[LightGBM] [Info] Number of data points in the train set: 2741, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=11, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=11
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 122000016.000000
[LightGBM] [Warning] No further splits with positive gain, bes

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:32:44,114] Trial 29 finished with value: 32958641.23352144 and parameters: {'n_estimators': 621, 'learning_rate': 0.05078818177602985, 'max_depth': 12, 'num_leaves': 85, 'subsample': 0.8085801784432103, 'colsample_bytree': 0.9922283959827507, 'min_data_in_leaf': 11}. Best is trial 26 with value: 31589136.339236822.


[LightGBM] [Warning] min_data_in_leaf is set=11, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=11


In [ ]:
print('Best hyperparameters:', study_lh.best_params)
print('Best RMSE:', study_lh.best_value)

Best hyperparameters: {'n_estimators': 642, 'learning_rate': 0.046864984610650244, 'max_depth': 13, 'num_leaves': 79, 'subsample': 0.9014847512413454, 'colsample_bytree': 0.9798119220405977, 'min_data_in_leaf': 8}
Best RMSE: 31589136.339236822


In [ ]:
################# itog ########################
gbm_lh = LGBMRegressor(n_estimators = 511, learning_rate=0.049641450239224616, max_depth=10, num_leaves=99,
                    subsample=0.9145013355037311, colsample_bytree=0.8215877247105206, min_data_in_leaf=5,
                      objective='quantile', alpha=0.7, random_state=13)

In [ ]:
mlf_l(gbm_lh, X_train_high_l, X_test_high_l, y_train_high_l, y_test_high_l)

[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000413 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 674
[LightGBM] [Info] Number of data points in the train set: 2741, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 85000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

In [ ]:
filename = 'lightgbm_high'
pickle.dump(gbm_lh, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_high_l)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_high_l, y_pred)))

[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
root mean squared error :  29643657.124104757


# Lightgbm для moscow_medium

In [ ]:
moscow_medium_l = pd.get_dummies(moscow_medium, columns=['renovation', 'district'], drop_first=True, dtype='int64')
X_lm = moscow_medium_l.drop(columns=['price'])
y_lm = moscow_medium_l.price

X_train_medium_l, X_test_medium_l, y_train_medium_l, y_test_medium_l = train_test_split(X_lm, y_lm, train_size = 0.7, shuffle=True, random_state=13)

In [ ]:
X_lm

is_new  minutes  rooms    area  kit_area  floor  num_of_floors  \
326         0      1.0    3.0  104.00      20.0    3.0             15   
333         0      7.0    3.0   75.70       5.0    7.0             17   
341         0      5.0    3.0   90.53      14.1   10.0             21   
345         0     17.0    3.0   82.20       7.6   37.0             41   
346         0     15.0    3.0   91.40       7.1   10.0             41   
...       ...      ...    ...     ...       ...    ...            ...   
22641       1      7.0    2.0   85.00      13.7    5.0             22   
22642       1      7.0    2.0   79.90      13.3    6.0             22   
22643       1      7.0    2.0   80.20      13.3    8.0             22   
22644       1      7.0    2.0   75.70      12.9    5.0             22   
22645       1      7.0    1.0   40.20       9.2   15.0             13   

       renovation_Designer  renovation_European-style renovation  \
326                      1                                     0   
333                      1                                     0   
341                      0                                     1   
345                      0                                     0   
346                      1                                     0   
...                    ...                                   ...   
22641                    0                                     0   
22642                    0                                     0   
22643                    0                                     0   
22644                    0                                     0   
22645                    0                                     0   

       renovation_Without renovation  district_szao  district_uao  \
326                                0              0             0   
333                                0              0             0   
341                                0              0             0   
345                                1              0             0   
346                                0              0             0   
...                              ...            ...           ...   
22641                              0              0             1   
22642                              0              0             1   
22643                              0              0             1   
22644                              0              0             1   
22645                              0              0             1   

       district_uzao  
326                0  
333                0  
341                0  
345                0  
346                0  
...              ...  
22641              0  
22642              0  
22643              0  
22644              0  
22645              0  

[4824 rows x 13 columns]

In [ ]:
gbm_m = LGBMRegressor(num_leaves=31,
                    learning_rate=0.05,
                    n_estimators=20,
                    random_state=13)
gbm_m.fit(X_train_medium_l, y_train_medium_l,
        eval_set=[(X_test_medium_l, y_test_medium_l)],
        eval_metric='rmse')

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001378 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 658
[LightGBM] [Info] Number of data points in the train set: 3396, number of used features: 13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 28672997.079800


LGBMRegressor(learning_rate=0.05, n_estimators=20, random_state=13)

In [ ]:
mlf_l(gbm_m, X_train_medium_l, X_test_medium_l, y_train_medium_l, y_test_medium_l)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000186 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 658
[LightGBM] [Info] Number of data points in the train set: 3396, number of used features: 13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 28672997.079800

Model Report
RMSE for train: 21119754.822563875
r2 for train: 0.7207684951098188, 

RMSE for test: 20009792.017417457
r2 for test: 0.7216120268724964


In [ ]:
def objective_lm(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 800, 1300),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 6, 13),
        "num_leaves": trial.suggest_int("num_leaves", 60, 110),
        "subsample": trial.suggest_float("subsample", 0.7, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.7, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 10),
    }

    model = LGBMRegressor(**params, objective='quantile', alpha=0.8, random_state=13)
    model.fit(X_train_medium_l, y_train_medium_l, eval_set=(X_test_medium_l, y_test_medium_l), eval_metric='rmse')
    predictions = model.predict(X_test_medium_l)
    rmse = metrics.mean_squared_error(y_test_medium_l, predictions, squared=False)
    return rmse

In [ ]:
study_lm = optuna.create_study(direction='minimize')
study_lm.optimize(objective_lm, n_trials=30)

[I 2024-12-11 10:55:42,157] A new study created in memory with name: no-name-fa687c58-9377-437d-abc2-0c8bddbe89a8


[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000563 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 650
[LightGBM] [Info] Number of data points in the train set: 3376, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 34000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:55:43,866] Trial 0 finished with value: 11012553.210001545 and parameters: {'n_estimators': 977, 'learning_rate': 0.08161135060721446, 'max_depth': 10, 'num_leaves': 61, 'subsample': 0.9272430111364891, 'colsample_bytree': 0.7053531890263639, 'min_data_in_leaf': 2}. Best is trial 0 with value: 11012553.210001545.


[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000681 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 650
[LightGBM] [Info] Number of data points in the train set: 3376, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=10, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=10
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 34000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:55:46,372] Trial 1 finished with value: 15152984.041811388 and parameters: {'n_estimators': 1157, 'learning_rate': 0.0007909757125232242, 'max_depth': 9, 'num_leaves': 82, 'subsample': 0.8621250354413414, 'colsample_bytree': 0.9514076718391156, 'min_data_in_leaf': 10}. Best is trial 0 with value: 11012553.210001545.


...

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:56:59,633] Trial 27 finished with value: 10639473.021825818 and parameters: {'n_estimators': 988, 'learning_rate': 0.052270480528158726, 'max_depth': 9, 'num_leaves': 100, 'subsample': 0.747371649459583, 'colsample_bytree': 0.8194621140327527, 'min_data_in_leaf': 1}. Best is trial 27 with value: 10639473.021825818.


[LightGBM] [Warning] min_data_in_leaf is set=1, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=1
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=1, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=1
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000694 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 650
[LightGBM] [Info] Number of data points in the train set: 3376, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=1, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=1
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 34000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:57:01,988] Trial 28 finished with value: 11173350.579342334 and parameters: {'n_estimators': 839, 'learning_rate': 0.010992227489785612, 'max_depth': 7, 'num_leaves': 100, 'subsample': 0.7504868246448503, 'colsample_bytree': 0.8147503873783805, 'min_data_in_leaf': 1}. Best is trial 27 with value: 10639473.021825818.


[LightGBM] [Warning] min_data_in_leaf is set=3, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=3
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=3, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=3
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000572 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 650
[LightGBM] [Info] Number of data points in the train set: 3376, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=3, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=3
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 34000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 10:57:04,623] Trial 29 finished with value: 11258111.728826413 and parameters: {'n_estimators': 977, 'learning_rate': 0.004350788812355168, 'max_depth': 9, 'num_leaves': 107, 'subsample': 0.7094224231821096, 'colsample_bytree': 0.863135711505625, 'min_data_in_leaf': 3}. Best is trial 27 with value: 10639473.021825818.


In [ ]:
print('Best hyperparameters:', study_lm.best_params)
print('Best RMSE:', study_lm.best_value)

Best hyperparameters: {'n_estimators': 988, 'learning_rate': 0.052270480528158726, 'max_depth': 9, 'num_leaves': 100, 'subsample': 0.747371649459583, 'colsample_bytree': 0.8194621140327527, 'min_data_in_leaf': 1}
Best RMSE: 10639473.021825818


In [ ]:
################# itog ########################
gbm_lm = LGBMRegressor(n_estimators = 988, learning_rate=0.052270480528158726, max_depth=9, num_leaves=100,
                    subsample=0.747371649459583, colsample_bytree=0.8194621140327527, min_data_in_leaf=1,
                       objective='quantile', alpha=0.8, random_state=13)
mlf_l(gbm_lm, X_train_medium_l, X_test_medium_l, y_train_medium_l, y_test_medium_l)

[LightGBM] [Warning] min_data_in_leaf is set=1, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=1
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=1, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=1
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000754 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 650
[LightGBM] [Info] Number of data points in the train set: 3376, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=1, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=1
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 34000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

In [ ]:
filename = 'lightgbm_medium'
pickle.dump(gbm_lm, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_medium_l)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_medium_l, y_pred)))

[LightGBM] [Warning] min_data_in_leaf is set=1, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=1
root mean squared error :  10639473.021825818


# Lightgbm для moscow_low

In [ ]:
moscow_low_l = pd.get_dummies(moscow_low, columns=['renovation', 'district'], drop_first=True, dtype='int64')
X_ll = moscow_low_l.drop(columns=['price'])
y_ll = moscow_low_l.price

X_train_low_l, X_test_low_l, y_train_low_l, y_test_low_l = train_test_split(X_ll, y_ll, train_size = 0.7, shuffle=True, random_state=13)

In [ ]:
X_ll

is_new  minutes  rooms   area  kit_area  floor  num_of_floors  \
322         0     11.0    3.0   92.0      20.0    4.0             21   
323         0     13.0    3.0  109.0      25.0   35.0             58   
325         0      7.0    3.0   83.5      12.5   16.0             22   
327         0     10.0    3.0   77.1      13.5   22.0             25   
371         0      7.0    3.0   90.8      12.6    2.0             30   
...       ...      ...    ...    ...       ...    ...            ...   
22267       1     13.0    2.0   32.1       3.8   15.0             11   
22269       1     11.0    1.0   34.0      11.0   14.0             23   
22272       1     15.0    2.0   65.6      11.5   25.0             16   
22301       1     13.0    3.0   79.0       9.0    9.0             16   
22646       1     17.0    1.0   43.9      13.3   21.0             13   

       renovation_Designer  renovation_European-style renovation  \
322                      0                                     0   
323                      1                                     0   
325                      0                                     0   
327                      0                                     0   
371                      0                                     0   
...                    ...                                   ...   
22267                    0                                     0   
22269                    0                                     0   
22272                    0                                     0   
22301                    0                                     0   
22646                    0                                     0   

       renovation_Without renovation  district_svao  district_uvao  \
322                                0              1              0   
323                                0              1              0   
325                                1              1              0   
327                                1              0              0   
371                                0              0              0   
...                              ...            ...            ...   
22267                              0              0              1   
22269                              0              0              1   
22272                              0              0              1   
22301                              0              0              1   
22646                              0              0              1   

       district_vao  
322               0  
323               0  
325               0  
327               0  
371               1  
...             ...  
22267             0  
22269             0  
22272             0  
22301             0  
22646             0  

[5612 rows x 13 columns]

In [ ]:
gbm_l = LGBMRegressor(num_leaves=31,
                    learning_rate=0.05,
                    n_estimators=20,
                    random_state=13)
gbm_l.fit(X_train_low_l, y_train_low_l,
        eval_set=[(X_test_low_l, y_test_low_l)],
        eval_metric='rmse')

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000194 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 577
[LightGBM] [Info] Number of data points in the train set: 3928, number of used features: 13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 12580659.904022


LGBMRegressor(learning_rate=0.05, n_estimators=20, random_state=13)

In [ ]:
mlf_l(gbm_l, X_train_low_l, X_test_low_l, y_train_low_l, y_test_low_l)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000221 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 577
[LightGBM] [Info] Number of data points in the train set: 3928, number of used features: 13
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 12580659.904022

Model Report
RMSE for train: 4843361.490809972
r2 for train: 0.7350885021993419, 

RMSE for test: 5288790.251956653
r2 for test: 0.7070601808667554


In [ ]:
def objective_ll(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 600, 1000),
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 6, 11),
        "num_leaves": trial.suggest_int("num_leaves", 70, 90),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.7, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 8),
    }

    model = LGBMRegressor(**params, objective='quantile', alpha=0.8, random_state=13)
    model.fit(X_train_low_l, y_train_low_l, eval_set=(X_test_low_l, y_test_low_l), eval_metric='rmse')
    predictions = model.predict(X_test_low_l)
    rmse = metrics.mean_squared_error(y_test_low_l, predictions, squared=False)
    return rmse

In [ ]:
study_ll = optuna.create_study(direction='minimize')
study_ll.optimize(objective_ll, n_trials=30)

[I 2024-12-11 11:11:13,692] A new study created in memory with name: no-name-77fdb05d-3ac4-44b5-9d75-3357b0e3e991


[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000770 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 577
[LightGBM] [Info] Number of data points in the train set: 3928, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 15000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:11:15,934] Trial 0 finished with value: 3008480.817399717 and parameters: {'n_estimators': 858, 'learning_rate': 0.020380362309439883, 'max_depth': 7, 'num_leaves': 73, 'subsample': 0.7062313323991941, 'colsample_bytree': 0.7871407718986974, 'min_data_in_leaf': 5}. Best is trial 0 with value: 3008480.817399717.


[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] min_data_in_leaf is set=8, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=8
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=8, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=8
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000161 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 577
[LightGBM] [Info] Number of data points in the train set: 3928, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=8, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=8
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:11:17,459] Trial 1 finished with value: 3112707.0474470966 and parameters: {'n_estimators': 720, 'learning_rate': 0.007657129844634705, 'max_depth': 7, 'num_leaves': 74, 'subsample': 0.8703542148945032, 'colsample_bytree': 0.9572587664751145, 'min_data_in_leaf': 8}. Best is trial 0 with value: 3008480.817399717.


...

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:12:11,838] Trial 27 finished with value: 5233558.109932735 and parameters: {'n_estimators': 820, 'learning_rate': 0.0013233858423601723, 'max_depth': 8, 'num_leaves': 77, 'subsample': 0.6213288552009714, 'colsample_bytree': 0.8582655651801875, 'min_data_in_leaf': 3}. Best is trial 22 with value: 2793649.75009527.


[LightGBM] [Warning] min_data_in_leaf is set=3, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=3
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000603 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 577
[LightGBM] [Info] Number of data points in the train set: 3928, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 15000000.000000
[LightGBM] [W

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:12:13,499] Trial 28 finished with value: 2806580.9251526105 and parameters: {'n_estimators': 775, 'learning_rate': 0.01136498970354155, 'max_depth': 9, 'num_leaves': 80, 'subsample': 0.6774437806450634, 'colsample_bytree': 0.7806738848762675, 'min_data_in_leaf': 2}. Best is trial 22 with value: 2793649.75009527.


[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000123 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 577
[LightGBM] [Info] Number of data points in the train set: 3928, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 15000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain:

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:12:15,714] Trial 29 finished with value: 2853793.368346183 and parameters: {'n_estimators': 760, 'learning_rate': 0.024546740736930688, 'max_depth': 9, 'num_leaves': 73, 'subsample': 0.682599454401896, 'colsample_bytree': 0.793596447942576, 'min_data_in_leaf': 6}. Best is trial 22 with value: 2793649.75009527.


In [ ]:
print('Best hyperparameters:', study_ll.best_params)
print('Best RMSE:', study_ll.best_value)

Best hyperparameters: {'n_estimators': 877, 'learning_rate': 0.010677947774717648, 'max_depth': 8, 'num_leaves': 80, 'subsample': 0.6032484653619365, 'colsample_bytree': 0.773500846060697, 'min_data_in_leaf': 2}
Best RMSE: 2793649.75009527


In [ ]:
################# itog ########################
gbm_l = LGBMRegressor(n_estimators = 787, learning_rate=0.040453498263892836, max_depth=7, num_leaves=81,
                    subsample=0.6929403320408208, colsample_bytree=0.9367609150417758, min_data_in_leaf=2,
                      objective='quantile', alpha=0.8, random_state=13)
mlf_l(gbm_l, X_train_low_l, X_test_low_l, y_train_low_l, y_test_low_l)

[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000760 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 577
[LightGBM] [Info] Number of data points in the train set: 3928, number of used features: 13
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 15000000.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,

In [ ]:
filename = 'lightgbm_low'
pickle.dump(gbm_l, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_low_l)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_low_l, y_pred)))

[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
root mean squared error :  2788123.8816274684


# Lightgbm для region

In [ ]:
region_l = pd.get_dummies(region, columns=['renovation'], drop_first=True, dtype='int64')
X_lr = region_l.drop(columns=['price'])
y_lr = region_l.price

X_train_region_l, X_test_region_l, y_train_region_l, y_test_region_l = train_test_split(X_lr, y_lr, train_size = 0.7, shuffle=True, random_state=13)

In [ ]:
X_lr

is_new  minutes  rooms   area  kit_area  floor  num_of_floors  \
0           0      6.0    1.0  30.60       8.5   25.0             25   
1           0      2.0    1.0  49.20      10.0    6.0             15   
2           0     14.0    1.0  44.70      13.1   10.0             25   
3           0      8.0    1.0  35.10      11.0   12.0             33   
4           0      6.0    1.0  37.70       4.0    5.0              5   
...       ...      ...    ...    ...       ...    ...            ...   
22670       1      8.0    1.0  44.17      10.3    4.0             17   
22672       1     25.0    1.0  31.60      12.2   11.0             15   
22673       1     30.0    0.0  18.00       8.1   17.0             17   
22674       1     14.0    2.0  36.39       6.6   12.0             14   
22675       1      8.0    2.0  56.13       5.0   10.0             17   

       renovation_Designer  renovation_European-style renovation  \
0                        0                                     0   
1                        0                                     1   
2                        0                                     0   
3                        0                                     1   
4                        0                                     0   
...                    ...                                   ...   
22670                    0                                     0   
22672                    0                                     0   
22673                    0                                     0   
22674                    0                                     0   
22675                    0                                     0   

       renovation_Without renovation  
0                                  0  
1                                  0  
2                                  0  
3                                  0  
4                                  1  
...                              ...  
22670                              0  
22672                              0  
22673                              0  
22674                              0  
22675                              0  

[6068 rows x 10 columns]

In [ ]:
gbm_r = LGBMRegressor(num_leaves=31,
                    learning_rate=0.05,
                    n_estimators=20,
                    random_state=13)
gbm_r.fit(X_train_region_l, y_train_region_l,
        eval_set=[(X_test_region_l, y_test_region_l)],
        eval_metric='rmse')

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000997 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 513
[LightGBM] [Info] Number of data points in the train set: 4247, number of used features: 10
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 7019104.048269


LGBMRegressor(learning_rate=0.05, n_estimators=20, random_state=13)

In [ ]:
mlf_l(gbm_r, X_train_region_l, X_test_region_l, y_train_region_l, y_test_region_l)

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000354 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 513
[LightGBM] [Info] Number of data points in the train set: 4247, number of used features: 10
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 7019104.048269

Model Report
RMSE for train: 1447077.312460486
r2 for train: 0.729246056946959, 

RMSE for test: 1590988.4764482966
r2 for test: 0.7036582419970967


In [ ]:
def objective_lr(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 500, 900),
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 7, 15),
        "num_leaves": trial.suggest_int("num_leaves", 70, 120),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.7, 1.0),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 10),
    }

    model = LGBMRegressor(**params, objective='quantile', alpha=0.8, random_state=13)
    model.fit(X_train_region_l, y_train_region_l, eval_set=(X_test_region_l, y_test_region_l), eval_metric='rmse')
    predictions = model.predict(X_test_region_l)
    rmse = metrics.mean_squared_error(y_test_region_l, predictions, squared=False)
    return rmse

In [ ]:
study_lr = optuna.create_study(direction='minimize')
study_lr.optimize(objective_lr, n_trials=30)

[I 2024-12-11 11:18:48,895] A new study created in memory with name: no-name-f9cb6a3c-116a-4cb0-a128-8a8caacf0b29


[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=7
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=7
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000535 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 513
[LightGBM] [Info] Number of data points in the train set: 4247, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=7
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 8714711.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:18:50,022] Trial 0 finished with value: 2286145.9382904107 and parameters: {'n_estimators': 526, 'learning_rate': 0.0013571028485059808, 'max_depth': 9, 'num_leaves': 93, 'subsample': 0.7723619374063218, 'colsample_bytree': 0.8875589538153335, 'min_data_in_leaf': 7}. Best is trial 0 with value: 2286145.9382904107.


[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=7
[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000525 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 513
[LightGBM] [Info] Number of data points in the train set: 4247, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=6, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=6
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 8714711.000000


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:18:51,303] Trial 1 finished with value: 2173524.508211178 and parameters: {'n_estimators': 681, 'learning_rate': 0.001301898020143746, 'max_depth': 13, 'num_leaves': 72, 'subsample': 0.7844260090310763, 'colsample_bytree': 0.732211071937954, 'min_data_in_leaf': 6}. Best is trial 1 with value: 2173524.508211178.


...

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:19:45,478] Trial 27 finished with value: 911581.3216281224 and parameters: {'n_estimators': 815, 'learning_rate': 0.07921238896705542, 'max_depth': 9, 'num_leaves': 113, 'subsample': 0.6760858639279871, 'colsample_bytree': 0.8502528298694827, 'min_data_in_leaf': 2}. Best is trial 10 with value: 872725.7174049517.


[LightGBM] [Warning] min_data_in_leaf is set=4, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=4
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=4, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=4
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000525 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 513
[LightGBM] [Info] Number of data points in the train set: 4247, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=4, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=4
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 8714711.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:19:47,685] Trial 28 finished with value: 919197.2780628641 and parameters: {'n_estimators': 864, 'learning_rate': 0.044243804582338515, 'max_depth': 11, 'num_leaves': 105, 'subsample': 0.7112602238852423, 'colsample_bytree': 0.7938118343690709, 'min_data_in_leaf': 4}. Best is trial 10 with value: 872725.7174049517.


[LightGBM] [Warning] min_data_in_leaf is set=9, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=9
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=9, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=9
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000528 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 513
[LightGBM] [Info] Number of data points in the train set: 4247, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=9, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=9
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 8714711.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 11:19:49,879] Trial 29 finished with value: 1052961.3479290633 and parameters: {'n_estimators': 746, 'learning_rate': 0.022325611661098067, 'max_depth': 12, 'num_leaves': 120, 'subsample': 0.7576648341588667, 'colsample_bytree': 0.7528640783692536, 'min_data_in_leaf': 9}. Best is trial 10 with value: 872725.7174049517.


In [ ]:
print('Best hyperparameters:', study_lr.best_params)
print('Best RMSE:', study_lr.best_value)

Best hyperparameters: {'n_estimators': 893, 'learning_rate': 0.026451410594000878, 'max_depth': 10, 'num_leaves': 114, 'subsample': 0.6009328657906645, 'colsample_bytree': 0.8631260140727859, 'min_data_in_leaf': 1}
Best RMSE: 872725.7174049517


In [ ]:
################# itog ########################
gbm_r = LGBMRegressor(n_estimators = 572, learning_rate=0.09246489912147637, max_depth=13, num_leaves=115,
                    subsample=0.7197009670544868, colsample_bytree=0.7530099102589622, min_data_in_leaf=2,
                      objective='quantile', alpha=0.8, random_state=13)
mlf_l(gbm_r, X_train_region_l, X_test_region_l, y_train_region_l, y_test_region_l)

[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000879 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 513
[LightGBM] [Info] Number of data points in the train set: 4247, number of used features: 10
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 8714711.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

In [ ]:
filename = 'lightgbm_region'
pickle.dump(gbm_r, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_region_l)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_region_l, y_pred)))

[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
root mean squared error :  857215.9796258013


# XGBoost для moscow_high

In [ ]:
from matplotlib import pylab as plot
import matplotlib.pyplot as plt
%pylab inline

import xgboost as xgb
from xgboost.sklearn import XGBRegressor

Populating the interactive namespace from numpy and matplotlib


/usr/local/lib/python3.10/dist-packages/IPython/core/magics/pylab.py:159: UserWarning: pylab import has clobbered these variables: ['plot']
`%matplotlib` prevents importing * from pylab and numpy
  warn("pylab import has clobbered these variables: %s"  % clobbered +


In [ ]:
moscow_high_x = pd.get_dummies(moscow_high, columns=['renovation', 'district'], drop_first=True, dtype='int64')

In [ ]:
high_xgb = XGBRegressor(learning_rate=0.1,
                          n_estimators=150,
                          objective= 'reg:quantile',
                          alpha=0.7,
                          nthread=-1,
                          scale_pos_weight=1,
                          seed=13)

In [ ]:
X = moscow_high_x.drop(columns=['price'])
y = moscow_high_x.price

X_train_high, X_test_high, y_train_high, y_test_high = train_test_split(X, y, train_size = 0.7, shuffle=True, random_state=13)

In [ ]:
def modelfit(alg, X_train, X_test, y_train, y_test, early_stopping_rounds=50):

  #Fit the algorithm on the data
  alg.fit(
    X_train, y_train
  )

  #Predict training set:
  dtrain_predictions = alg.predict(X_train)

  #Print model report:
  print("\nModel Report")
  print(f"RMSE for train: {metrics.root_mean_squared_error(y_train, dtrain_predictions)}")
  print(f"r2 for train: {metrics.r2_score(y_train, dtrain_predictions)}, \n")

  #Predict on testing data:
  dtest_predictions = alg.predict(X_test)
  print(f"RMSE for test: {metrics.root_mean_squared_error(y_test, dtest_predictions)}")
  print(f"r2 for test: {metrics.r2_score(y_test, dtest_predictions)}")

In [ ]:
modelfit(high_xgb, X_train_high, X_test_high, y_train_high, y_test_high)

/usr/local/lib/python3.10/dist-packages/xgboost/core.py:158: UserWarning: [13:22:54] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "scale_pos_weight" } are not used.

  warnings.warn(smsg, UserWarning)



Model Report
RMSE for train: 80166930.82377683
r2 for train: 0.7012548814888053, 

RMSE for test: 82934224.72159183
r2 for test: 0.700411045213249


In [ ]:
def objective_xh(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 900, 1200),
        "learning_rate": trial.suggest_float("learning_rate", 1e-3, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 6, 13),
        "subsample": trial.suggest_float("subsample", 0.7, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
        "min_child_weight": trial.suggest_int("min_child_weight", 12, 35),
        "gamma": trial.suggest_float("gamma", 1e-3, 0.1),
        "reg_alpha": trial.suggest_float("reg_alpha", 1e-2, 5),
    }

    model = XGBRegressor(**params, objective= 'reg:quantileerror', quantile_alpha=0.8, seed=13)
    model.fit(X_train_high, y_train_high)
    predictions = model.predict(X_test_high)
    rmse = metrics.mean_squared_error(y_test_high, predictions, squared=False)
    return rmse

In [ ]:
study_xh = optuna.create_study(direction='minimize')
study_xh.optimize(objective_xh, n_trials=30)

[I 2024-12-11 12:08:22,118] A new study created in memory with name: no-name-48820485-dbda-4a88-a96f-54e17cac797c
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 12:08:27,399] Trial 0 finished with value: 37917005.191754535 and parameters: {'n_estimators': 1068, 'learning_rate': 0.056406907502952366, 'max_depth': 13, 'subsample': 0.8232316671290382, 'colsample_bytree': 0.9758758746909955, 'min_child_weight': 19, 'gamma': 0.09896458837933378, 'reg_alpha': 3.806935354569255}. Best is trial 0 with value: 37917005.191754535.
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  wa

In [ ]:
print('Best hyperparameters:', study_xh.best_params)
print('Best RMSE:', study_xh.best_value)

Best hyperparameters: {'n_estimators': 1025, 'learning_rate': 0.04237557420025514, 'max_depth': 12, 'subsample': 0.8035433824565256, 'colsample_bytree': 0.66269751398511, 'min_child_weight': 18, 'gamma': 0.06802170691764002, 'reg_alpha': 0.5476227463850738}
Best RMSE: 33194800.554730598


In [ ]:
################# itog ########################
high_xgb = XGBRegressor(learning_rate=0.05441611087463926,
                          n_estimators=1073,
                          max_depth=9,
                          subsample = 0.9639152578524065,
                          colsample_bytree = 0.7068144966129117,
                          min_child_weight=22,
                          gamma=0.043008454856764015,
                          reg_alpha=0.5665267752449539,
                          objective= 'reg:quantileerror',
                          quantile_alpha=0.7,
                          nthread=-1,
                          scale_pos_weight=1,
                          seed=13)
modelfit(high_xgb, X_train_high, X_test_high, y_train_high, y_test_high)

/usr/local/lib/python3.10/dist-packages/xgboost/core.py:158: UserWarning: [12:07:36] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "scale_pos_weight" } are not used.

  warnings.warn(smsg, UserWarning)



Model Report
RMSE for train: 20075112.91101773
r2 for train: 0.9055355446399047, 

RMSE for test: 31061735.35824868
r2 for test: 0.7697930824082315


In [ ]:
filename = 'xgboost_high'
pickle.dump(high_xgb, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_high)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_high, y_pred)))

root mean squared error :  31061735.35824868


# XGBoost для moscow_medium

In [ ]:
moscow_medium_x = pd.get_dummies(moscow_medium, columns=['renovation', 'district'], drop_first=True, dtype='int64')

In [ ]:
medium_xgb = XGBRegressor(learning_rate=0.1,
                          n_estimators=150,
                          objective= 'reg:squarederror',
                          nthread=-1,
                          scale_pos_weight=1,
                          seed=13)

In [ ]:
X_medium = moscow_medium_x.drop(columns=['price'])
y_medium = moscow_medium_x.price

X_train_medium, X_test_medium, y_train_medium, y_test_medium = train_test_split(X_medium, y_medium, train_size = 0.7, shuffle=True, random_state=13)

In [ ]:
def objective_xm(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 750, 1100),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 5, 13),
        "subsample": trial.suggest_float("subsample", 0.5, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
        "min_child_weight": trial.suggest_int("min_child_weight", 3, 15),
        "gamma": trial.suggest_float("gamma", 1e-4, 0.5),
        "reg_alpha": trial.suggest_float("reg_alpha", 1, 10),
    }

    model = XGBRegressor(**params, objective= 'reg:quantileerror', quantile_alpha=0.7,  seed=13)
    model.fit(X_train_medium, y_train_medium)
    predictions = model.predict(X_test_medium)
    rmse = metrics.mean_squared_error(y_test_medium, predictions, squared=False)
    return rmse

In [ ]:
study_xm = optuna.create_study(direction='minimize')
study_xm.optimize(objective_xm, n_trials=30)

[I 2024-12-11 12:21:42,183] A new study created in memory with name: no-name-e9085f4f-e706-48ad-880b-51e83557b663
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 12:21:43,292] Trial 0 finished with value: 11688120.767250719 and parameters: {'n_estimators': 989, 'learning_rate': 0.04777945957582733, 'max_depth': 10, 'subsample': 0.7093734388393069, 'colsample_bytree': 0.919024579897937, 'min_child_weight': 10, 'gamma': 0.41198959583940614, 'reg_alpha': 4.079775211040029}. Best is trial 0 with value: 11688120.767250719.
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warni

In [ ]:
print('Best hyperparameters:', study_xm.best_params)
print('Best RMSE:', study_xm.best_value)

Best hyperparameters: {'n_estimators': 847, 'learning_rate': 0.017125662668407857, 'max_depth': 13, 'subsample': 0.824224997184994, 'colsample_bytree': 0.7706963460573254, 'min_child_weight': 4, 'gamma': 0.2913469373707511, 'reg_alpha': 1.0452863874219096}
Best RMSE: 10805201.315830743


In [ ]:
################# itog ########################
medium_xgb = XGBRegressor(**study_xm.best_params,
                          objective= 'reg:quantileerror',
                          quantile_alpha=0.7,
                          nthread=-1,
                          scale_pos_weight=1,
                          seed=13)
modelfit(medium_xgb, X_train_medium, X_test_medium, y_train_medium, y_test_medium)

/usr/local/lib/python3.10/dist-packages/xgboost/core.py:158: UserWarning: [12:23:16] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "scale_pos_weight" } are not used.

  warnings.warn(smsg, UserWarning)



Model Report
RMSE for train: 6894027.172829182
r2 for train: 0.9478409033035132, 

RMSE for test: 10805201.315830743
r2 for test: 0.8342026656432612


In [ ]:
filename = 'xgboost_medium'
pickle.dump(medium_xgb, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_medium)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_medium, y_pred)))

root mean squared error :  10805201.315830743


# XGBoost для moscow_low

In [ ]:
moscow_low_x = pd.get_dummies(moscow_low, columns=['renovation', 'district'], drop_first=True, dtype='int64')

In [ ]:
moscow_low_x

price  is_new  minutes  rooms   area  kit_area  floor  \
322    52500000.0       0     11.0    3.0   92.0      20.0    4.0   
323    38000000.0       0     13.0    3.0  109.0      25.0   35.0   
325    22450000.0       0      7.0    3.0   83.5      12.5   16.0   
327    17500000.0       0     10.0    3.0   77.1      13.5   22.0   
371    33800000.0       0      7.0    3.0   90.8      12.6    2.0   
...           ...     ...      ...    ...    ...       ...    ...   
22267   7986480.0       1     13.0    2.0   32.1       3.8   15.0   
22269   9530000.0       1     11.0    1.0   34.0      11.0   14.0   
22272  15700000.0       1     15.0    2.0   65.6      11.5   25.0   
22301  13000000.0       1     13.0    3.0   79.0       9.0    9.0   
22646  12000000.0       1     17.0    1.0   43.9      13.3   21.0   

       num_of_floors  renovation_Designer  \
322               21                    0   
323               58                    1   
325               22                    0   
327               25                    0   
371               30                    0   
...              ...                  ...   
22267             11                    0   
22269             23                    0   
22272             16                    0   
22301             16                    0   
22646             13                    0   

       renovation_European-style renovation  renovation_Without renovation  \
322                                       0                              0   
323                                       0                              0   
325                                       0                              1   
327                                       0                              1   
371                                       0                              0   
...                                     ...                            ...   
22267                                     0                              0   
22269                                     0                              0   
22272                                     0                              0   
22301                                     0                              0   
22646                                     0                              0   

       district_svao  district_uvao  district_vao  
322                1              0             0  
323                1              0             0  
325                1              0             0  
327                0              0             0  
371                0              0             1  
...              ...            ...           ...  
22267              0              1             0  
22269              0              1             0  
22272              0              1             0  
22301              0              1             0  
22646              0              1             0  

[5612 rows x 14 columns]

In [ ]:
low_xgb = XGBRegressor(learning_rate=0.1,
                          n_estimators=150,
                          objective= 'reg:squarederror',
                          nthread=-1,
                          scale_pos_weight=1,
                          seed=13)

In [ ]:
X_low = moscow_low_x.drop(columns=['price'])
y_low = moscow_low_x.price

X_train_low, X_test_low, y_train_low, y_test_low = train_test_split(X_low, y_low, train_size = 0.7, shuffle=True, random_state=13)

In [ ]:
X_train_low

is_new  minutes  rooms   area  kit_area  floor  num_of_floors  \
8219        0     16.0    3.0  68.80       9.5   19.0             22   
16797       1     19.0    2.0  62.41      11.8    2.0             11   
1775        0     15.0    1.0  34.90       9.0   11.0             12   
18231       1     13.0    1.0  40.16      10.0   13.0             16   
8834        0     23.0    3.0  60.00       6.0    9.0              9   
...       ...      ...    ...    ...       ...    ...            ...   
1735        0      6.0    1.0  39.00      10.1   18.0             33   
5072        0     12.0    1.0  39.00      10.0    6.0             22   
12217       0     25.0    0.0  17.00       2.0    1.0             12   
1519        0     13.0    0.0  28.00       9.0    5.0             10   
3396        0     10.0    2.0  57.10      14.0   24.0             29   

       renovation_Designer  renovation_European-style renovation  \
8219                     0                                     0   
16797                    0                                     0   
1775                     0                                     0   
18231                    0                                     0   
8834                     0                                     0   
...                    ...                                   ...   
1735                     0                                     1   
5072                     0                                     0   
12217                    0                                     0   
1519                     1                                     0   
3396                     0                                     1   

       renovation_Without renovation  district_svao  district_uvao  \
8219                               0              0              1   
16797                              0              0              1   
1775                               1              0              0   
18231                              0              0              1   
8834                               1              0              0   
...                              ...            ...            ...   
1735                               0              0              0   
5072                               0              0              1   
12217                              1              0              0   
1519                               0              1              0   
3396                               0              0              1   

       district_vao  
8219              0  
16797             0  
1775              1  
18231             0  
8834              1  
...             ...  
1735              1  
5072              0  
12217             1  
1519              0  
3396              0  

[3928 rows x 13 columns]

In [ ]:
def objective_xl(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 600, 1300),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 5, 13),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.65, 1.0),
        "min_child_weight": trial.suggest_int("min_child_weight", 1, 20),
        "gamma": trial.suggest_float("gamma", 1e-4, 0.1),
        "reg_alpha": trial.suggest_float("reg_alpha", 1e-2, 5),
    }

    model = XGBRegressor(**params, objective= 'reg:quantileerror', quantile_alpha=0.7, seed=13)
    model.fit(X_train_low, y_train_low)
    predictions = model.predict(X_test_low)
    rmse = metrics.mean_squared_error(y_test_low, predictions, squared=False)
    return rmse

In [ ]:
study_xl = optuna.create_study(direction='minimize')
study_xl.optimize(objective_xl, n_trials=30)

[I 2024-12-11 12:26:43,117] A new study created in memory with name: no-name-7a3e5036-06b7-42d1-ac6b-16102a4be1a2
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 12:26:44,904] Trial 0 finished with value: 8827188.22423794 and parameters: {'n_estimators': 1106, 'learning_rate': 0.0002083113972241228, 'max_depth': 7, 'subsample': 0.8782318458061835, 'colsample_bytree': 0.8899458821296686, 'min_child_weight': 19, 'gamma': 0.07896107670090872, 'reg_alpha': 4.3282300857595795}. Best is trial 0 with value: 8827188.22423794.
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warni

In [ ]:
print('Best hyperparameters:', study_xl.best_params)
print('Best RMSE:', study_xl.best_value)

Best hyperparameters: {'n_estimators': 953, 'learning_rate': 0.02224206149711645, 'max_depth': 7, 'subsample': 0.8882692978303469, 'colsample_bytree': 0.7744320991174012, 'min_child_weight': 1, 'gamma': 0.020333307651097664, 'reg_alpha': 2.8844848067273956}
Best RMSE: 2854155.228616525


In [ ]:
################# itog ########################
low_xgb = XGBRegressor(**study_xl.best_params,
                          objective= 'reg:quantileerror',
                          quantile_alpha=0.7,
                          nthread=-1,
                          scale_pos_weight=1,
                          seed=13)
modelfit(low_xgb, X_train_low, X_test_low, y_train_low, y_test_low)

/usr/local/lib/python3.10/dist-packages/xgboost/core.py:158: UserWarning: [12:28:00] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "scale_pos_weight" } are not used.

  warnings.warn(smsg, UserWarning)



Model Report
RMSE for train: 1969597.0751123421
r2 for train: 0.9561911532580758, 

RMSE for test: 2854155.228616525
r2 for test: 0.9146858829580954


In [ ]:
filename = 'xgboost_low'
pickle.dump(low_xgb, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_low)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_low, y_pred)))

root mean squared error :  2854155.228616525


#XGBoost для region

In [ ]:
region_r = pd.get_dummies(region, columns=['renovation'], drop_first=True, dtype='int64')

In [ ]:
region_xgb = XGBRegressor(learning_rate=0.1,
                          n_estimators=150,
                          objective= 'reg:squarederror',
                          nthread=-1,
                          scale_pos_weight=1,
                          seed=13)

In [ ]:
X_region = region_r.drop(columns=['price'])
y_region = region_r.price

X_train_region, X_test_region, y_train_region, y_test_region = train_test_split(X_region, y_region, train_size = 0.7, shuffle=True, random_state=13)

In [ ]:
X_region

is_new  minutes  rooms   area  kit_area  floor  num_of_floors  \
0           0      6.0    1.0  30.60       8.5   25.0             25   
1           0      2.0    1.0  49.20      10.0    6.0             15   
2           0     14.0    1.0  44.70      13.1   10.0             25   
3           0      8.0    1.0  35.10      11.0   12.0             33   
4           0      6.0    1.0  37.70       4.0    5.0              5   
...       ...      ...    ...    ...       ...    ...            ...   
22670       1      8.0    1.0  44.17      10.3    4.0             17   
22672       1     25.0    1.0  31.60      12.2   11.0             15   
22673       1     30.0    0.0  18.00       8.1   17.0             17   
22674       1     14.0    2.0  36.39       6.6   12.0             14   
22675       1      8.0    2.0  56.13       5.0   10.0             17   

       renovation_Designer  renovation_European-style renovation  \
0                        0                                     0   
1                        0                                     1   
2                        0                                     0   
3                        0                                     1   
4                        0                                     0   
...                    ...                                   ...   
22670                    0                                     0   
22672                    0                                     0   
22673                    0                                     0   
22674                    0                                     0   
22675                    0                                     0   

       renovation_Without renovation  
0                                  0  
1                                  0  
2                                  0  
3                                  0  
4                                  1  
...                              ...  
22670                              0  
22672                              0  
22673                              0  
22674                              0  
22675                              0  

[6068 rows x 10 columns]

In [ ]:
def objective_xr(trial):
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 300, 1200),
        "learning_rate": trial.suggest_float("learning_rate", 1e-4, 0.1, log=True),
        "max_depth": trial.suggest_int("max_depth", 3, 15),
        "subsample": trial.suggest_float("subsample", 0.4, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.4, 1.0),
        "min_child_weight": trial.suggest_int("min_child_weight", 1, 25),
        "gamma": trial.suggest_float("gamma", 1e-5, 0.1),
        "reg_alpha": trial.suggest_float("reg_alpha", 1e-2, 15),
    }

    model = XGBRegressor(**params, objective= 'reg:quantileerror', quantile_alpha=0.7, seed=13)
    model.fit(X_train_region, y_train_region)
    predictions = model.predict(X_test_region)
    rmse = metrics.mean_squared_error(y_test_region, predictions, squared=False)
    return rmse

In [ ]:
study_xr = optuna.create_study(direction='minimize')
study_xr.optimize(objective_xr, n_trials=30)

[I 2024-12-11 12:29:29,343] A new study created in memory with name: no-name-daf5c580-ce0b-4611-9526-a15217e5f3d8
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(
[I 2024-12-11 12:29:34,871] Trial 0 finished with value: 1127999.5453456293 and parameters: {'n_estimators': 1158, 'learning_rate': 0.030919705717016084, 'max_depth': 9, 'subsample': 0.8445675712778209, 'colsample_bytree': 0.9378829869205688, 'min_child_weight': 1, 'gamma': 0.07697914386482482, 'reg_alpha': 14.409914447241654}. Best is trial 0 with value: 1127999.5453456293.
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  war

In [ ]:
print('Best hyperparameters:', study_xr.best_params)
print('Best RMSE:', study_xr.best_value)

Best hyperparameters: {'n_estimators': 304, 'learning_rate': 0.04941122277172724, 'max_depth': 11, 'subsample': 0.7129840105610414, 'colsample_bytree': 0.8753435728872978, 'min_child_weight': 1, 'gamma': 0.018531035846643527, 'reg_alpha': 1.8502753441168096}
Best RMSE: 868759.3162333597


In [ ]:
################# itog ########################
region_xgb = XGBRegressor(**study_xr.best_params,
                          objective= 'reg:quantileerror',
                          quantile_alpha=0.7,
                          nthread=-1,
                          scale_pos_weight=1,
                          seed=13)
modelfit(region_xgb, X_train_region, X_test_region, y_train_region, y_test_region)

/usr/local/lib/python3.10/dist-packages/xgboost/core.py:158: UserWarning: [12:51:12] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "scale_pos_weight" } are not used.

  warnings.warn(smsg, UserWarning)



Model Report
RMSE for train: 484767.28208474413
r2 for train: 0.9696150922390273, 

RMSE for test: 868759.3162333597
r2 for test: 0.9116395875361131


In [ ]:
modelfit(region_xgb, X_train_region, X_test_region, y_train_region, y_test_region)

/usr/local/lib/python3.10/dist-packages/xgboost/core.py:158: UserWarning: [12:51:16] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "scale_pos_weight" } are not used.

  warnings.warn(smsg, UserWarning)



Model Report
RMSE for train: 484767.28208474413
r2 for train: 0.9696150922390273, 

RMSE for test: 868759.3162333597
r2 for test: 0.9116395875361131


In [ ]:
filename = 'xgboost_region'
pickle.dump(region_xgb, open(filename, 'wb'))

In [ ]:
load_model = pickle.load(open(filename, 'rb'))

y_pred = load_model.predict(X_test_region)
print('root mean squared error : ', np.sqrt(
    metrics.mean_squared_error(y_test_region, y_pred)))

root mean squared error :  868759.3162333597
